In [1]:
# importing libraries
from bs4 import BeautifulSoup
import requests
import json
import re
import urllib
import time
import logging

logger = logging.getLogger('scraper')
FORMAT = "[%(filename)s:%(lineno)s - %(funcName)20s() ] %(message)s"
logging.basicConfig(format=FORMAT)
#logger.setLevel(logging.DEBUG)
#logger.debug('your message') 

class web_scraping:
    def __init__(self, URL, data):
        self.URL = URL
        self.data = data

    # specifying user agent, You can use other user agents
    # available on the internet
        self.HEADERS = ({'User-Agent':
                'Mozilla/5.0 (X11; Linux x86_64)  AppleWebKit/537.36 (KHTML, like Gecko) Chrome/44.0.2403.157 Safari/537.36',
                                'Accept-Language': 'en-US, en;q=0.5'})
  
    # Making the HTTP Request
        self.webpage = requests.get(self.URL, headers=self.HEADERS)
  
    # Creating the Soup Object containing all data
        self.soup = BeautifulSoup(self.webpage.content, "lxml")
        

    # retreiving product title
    def product_title(self):
        try:
            title = self.soup.find("span", attrs={"id": 'productTitle'})          
            title_value = title.string        
            title_string = title_value.strip().replace(',', '')
            return title_string
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            title_string = "NA"
            return title_string
  

    # retreiving product brand
    def brand(self):
        try:
            title_string = 'NA'
            if self.soup.find("td", attrs={"class": 'a-span9'}):         
                title = self.soup.find("td", attrs={"class": 'a-span9'})
                title = title.find("span", attrs={'class': 'a-size-base'})        
                title_string = title.text
                return title_string
            return title_string
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            title_string = "NA"
            return title_string

    
    # retreiving product price
    def product_price(self):
        try:
            price = 'NA'
            if self.soup.find("span", attrs={'id': 'priceblock_ourprice'}):
                price = self.soup.find("span", attrs={'id': 'priceblock_ourprice'}).string.strip().replace(',', '')
                trim = re.compile(r'[^\d.,]+')
                result = trim.sub('', price)
                return result
            elif self.soup.find("span", attrs={'id': 'priceblock_dealprice'}):
                price = self.soup.find("span", attrs={'id': 'priceblock_dealprice'}).string.strip().replace(',', '')
                trim = re.compile(r'[^\d.,]+')
                result = trim.sub('', price)
                return result
            else:
                return price
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            result = 'NA'
            return result
  
    
    # retreiving product offers
    def offers(self):
        try:
            offers = 'NA'
            if self.soup.find("span", attrs={'class': 'saving-prompt'}):
                offers = self.soup.find("span", attrs={'class': 'saving-prompt'}).text
                return str(int(re.search(r'\d+', offers).group()))
            return offers
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            offers = "NA"
            return offers
    
    
    # retreiving strike product price
    def strike_product_price(self):
        try:
            price = 'NA'
            if self.soup.find("span", attrs={'class': 'priceBlockStrikePriceString a-text-strike'}):
                price = self.soup.find("span", attrs={'class': 'priceBlockStrikePriceString a-text-strike'}).text
                return str(float(re.search(r'\d+', price).group()))
            return price
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            price = "NA"
            return price
    
    
    # retreiving product fullfilled
    def fullfilled(self):
        try:
            fullfilled = 'NA'
            if self.soup.find("span", attrs={'class': 'a-icon-text-fba'}):
                fullfilled_soup = self.soup.find("span", attrs={'class': 'a-icon-text-fba'})
                fullfilled = fullfilled_soup.text
                return fullfilled
            return fullfilled
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            fullfilled = "NA"
            return fullfilled

    
    # retreiving product rating
    def rating(self):
        try:
            rating = self.soup.find("i", attrs={'class': 'a-icon a-icon-star a-star-4-5'}).string.strip().replace(',', '')
            return rating 
        except AttributeError:
            try:
                rating = self.soup.find("span", attrs={'class': 'a-icon-alt'}).string.strip().replace(',', '')
                return rating
            except Exception as e:
                logging.error("Exception occurred", exc_info=True)
                rating = "NA"
                return rating


    # retreiving product reviews
    def reviews(self):
        try:
            review_count = self.soup.find("span", attrs={'id': 'acrCustomerReviewText'}).string.strip().replace(',', '')
            return review_count
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            review_count = "NA"
            return review_count

  
    # print availiblility status
    def availability(self):
        try:
            available = self.soup.find("div", attrs={'id': 'availability'})
            if available.find("span", attrs={'class': 'a-size-medium a-color-state'}):
                available = available.find("span", attrs={'class': 'a-size-medium a-color-state'}).string.strip().replace(',', '')
                return available
            return 'NA'  
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            available = "NA"
            return available


    # retreiving product categories
    def categories(self):
        try:
            categories = []
            if self.soup.find("div", attrs={'id': 'showing-breadcrumbs_div'}):
                breadcrumbs_div = self.soup.find("div", attrs={'id': 'showing-breadcrumbs_div'})
                rating = breadcrumbs_div.find_all("span", attrs={'class': 'a-list-item'})
                for i in rating:
                    if len(i) > 1:
                        categories.append(i.text.strip().replace('›', ''))
                return categories
            return categories
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            categories = "NA"
            return categories
            

    # retreiving product icons
    def icons(self):
        try: 
            icon_list = []
            fullfilled_soup = self.soup.find("div", attrs={'class': 'a-row icon-farm-wrapper'})
            icons = fullfilled_soup.text.strip().replace('\n', '').split('  ')
            for i in icons:
                if len(i) > 1:
                    icon_list.append(i)
            return icon_list
        except Exception as e:
            logging.error("Exception occurred", exc_info=True)
            icon_list = []
            return icon_list

    
    # retreiving product details
    def product_details(self):
        try:
            if self.soup.find("div", attrs={'id': 'detailBullets_feature_div'}):
                features_div = self.soup.find("div", attrs={'id': 'detailBullets_feature_div'})
                features_ordered = features_div.find_all("span", attrs={'class': 'a-list-item'})
                prod_feat = {}    
                try:
                    for i in features_ordered:
                        feat = i.text.strip().replace("\n", "").split(":")
                        if len(feat) == 2:
                            prod_feat[feat[0]] = feat[1]
                    return prod_feat
                except Exception as e:
                    logging.error("Exception occurred", exc_info=True)
                    pass
            return {}
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            prod_feat = "NA"
            return prod_feat
            
    
    # retreiving product important infos
    def important_infos(self):
        try: 
            important_info = 'NA'
            if self.soup.find("div", attrs={'id': 'important-information'}):
                features_div = self.soup.find("div", attrs={'id': 'important-information'})
                important_info  = features_div.text.strip().replace("\n", "")
                return important_info
            return important_info
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            important_info = "NA" 
            return important_info  

    
    # retreiving product bought together
    def bought_together(self):    
        try:
            bought_together = []
            bought_together_div = self.soup.find("div", attrs={'id': 'sims-consolidated-1_feature_div'})
            if bought_together_div:
                features_ordered = bought_together_div.find_all("img", alt=True)
                for i in features_ordered:
                    if i['alt'] != '':
                        bought_together.append(i['alt'])
            return bought_together
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            bought_together = "NA"
            return bought_together
            
    
    # retreiving product subscription discount
    def subscription_discount(self):
        try: 
            subscription_discount = 'NA'
            if self.soup.find("span", attrs={'class': 'discountTextLeft'}):
                discount = self.soup.find("span", attrs={'class': 'discountTextLeft'})
                subscription_discount = discount.text
                return subscription_discount
            return subscription_discount
        except Exception as e:
            logging.error("Exception occurred", exc_info=True)
            subscription_discount = 'NA'
            return subscription_discount
            
  
    # retreiving product variations
    def variations(self):
        try:
            variations = []
            variations_div = self.soup.find("div", attrs={'id': 'variation_pattern_name'})
            if variations_div:
                variations_list = variations_div.find_all("img", attrs={'class': 'imgSwatch'})
                for i in variations_list:
                    variations.append(i['alt'])
            return variations
        except AttributeError as e:
            logging.error("Exception occurred", exc_info=True)
            variations = "NA"
            return variations
    

    # retreiving product data
    def Data(self):
        self.data["product Title"] = self.product_title()
        self.data["brand"] = self.brand() 
        self.data["Products price"] = self.product_price()
        # trim = re.compile(r'[^\d.,]+')
        # result = trim.sub('', self.offers())
        self.data["Offer_Count"] = self.offers()
        # trim = re.compile(r'[^\d.,]+')
        # result = trim.sub('', self.strike_product_price())
        self.data["StrikeThrough_Products_price"] = self.strike_product_price()
        self.data["Fullfilled"] = self.fullfilled()
        self.data["Overall rating"] = self.rating()
        self.data["Total reviews"] = self.reviews()
        self.data["Availability"] = self.availability()
        self.data["Category Tree"] = self.categories()
        self.data["icons"] = self.icons()
        self.data["Product_Details"] = self.product_details()
        self.data["misc_info"] = self.important_infos()
        self.data["bought_together"] = self.bought_together()
        self.data["subscription_discount"] = self.subscription_discount()
        self.data["variations"] = self.variations()
        return self.data
    

    def complete_data(self):
        data = []
        data.append(self.product_title())
        data.append(self.brand())
        data.append(self.product_price())
        data.append(self.offers())
        data.append(self.strike_product_price())
        data.append(self.fullfilled())
        data.append(self.rating())
        data.append(self.reviews())
        data.append(self.availability())
        data.append(self.categories())
        data.append(self.icons())
        data.append(self.product_details())
        data.append(self.important_infos())
        data.append(self.bought_together())
        data.append(self.subscription_discount())
        data.append(self.variations())
        return data

In [2]:
import pandas as pd
df = pd.read_csv("sh_url.csv")
urls = df['URL']

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
import csv

columns = ['product_title', 'brand', 'product_price', 'offer_count', 'strikethrough_products_price', 'fullfilled', 'overalll_rating', 'total_rewiews', 'availability', 'category_tree', 'icons', 'product_details', 'important_information', 'bought_together', 'sbuscription_discount', 'variations']

with open("data_output.csv", "w") as file:
    csvfile = csv.writer(file)
    csvfile.writerow(columns)
    for links in urls[0:50]:
        try:
            csvfile.writerow(web_scraping(links, {}).complete_data())
            time.sleep(5)
        except Exception as e:
            logging.error("Exception occurred", exc_info=True)
            print("-"*20 + " Exception " + "-"*20)

[<ipython-input-4-2603e98be883>:13 -             <module>() ] Exception occurred
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/urllib3/connection.py", line 159, in _new_conn
    (self._dns_host, self.port), self.timeout, **extra_kw)
  File "/usr/local/lib/python3.7/dist-packages/urllib3/util/connection.py", line 57, in create_connection
    for res in socket.getaddrinfo(host, port, family, socket.SOCK_STREAM):
  File "/usr/lib/python3.7/socket.py", line 752, in getaddrinfo
    for res in _socket.getaddrinfo(host, port, family, type, proto, flags):
socket.gaierror: [Errno -2] Name or service not known

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/urllib3/connectionpool.py", line 600, in urlopen
    chunked=chunked)
  File "/usr/local/lib/python3.7/dist-packages/urllib3/connectionpool.py", line 343, in _make_request
    self._validate_conn(conn)
  

-------------------- Exception --------------------


In [17]:
import pandas as pd
df = pd.read_csv("data_output.csv")
df

Halo Shampoo - 1 litre  ...                                               [].1
0   Indulekha Bringha Shampoo Ayurvedic Medicine F...  ...                                                 []
1   DABUR Vatika Ayurvedic Shampoo 640ml : Power o...  ...                                                 []
2   L'Oréal Professionnel Serie Expert Absolut Rep...  ...  ['Serie Expert Absolut Repair Shampoo', 'Serie...
3   Head & Shoulders  Anti Dandruff Shampoo Cool M...  ...  ['Hair Care & Styling+Shampoos', 'Shampoo', 'S...
4   WishCare® Fermented Rice Water Shampoo - Stren...  ...                                                 []
5   L'Oreal Paris Fall Resist 3X Anti-Hairfall Sha...  ...  ['Anti-Hairfall Shampoo', 'Anti-Hairfall Shamp...
6   Dove Hair Fall Rescue Shampoo For Weak Hair Pr...  ...                                                 []
7   Dabur Vatika Ayurvedic Shampoo for Hair Fall C...  ...                                                 []
8       Sunsilk Lusciously Thick & Long Shampoo 1 ltr  ...                                                 []
9              Scalpe Pro Anti-dandruff Shampoo 100ml  ...                                                 []
10  Head & Shoulders  Anti Dandruff Shampoo + Cond...  ...  ['Shampoo + Conditioner', 'Shampoo + Condition...
11                  Nyle Volume Enhance Shampoo 800ml  ...  ['Shampoo,Volume Enhance', 'Shampoo,Volume Enh...
12  mCaffeine Naked & Raw Coffee Shampoo | Hair Fa...  ...                                                 []
13          L'Oreal Paris Color Protect Shampoo 396ml  ...  ['Shampoo', 'Shampoo + Conditioner', 'Shampoo ...
14  Herbal Essences Vitamin E with Cocoa Butter SH...  ...                                                 []
15  Herbal Essences Coconut Milk SHAMPOO- For Hydr...  ...                                                 []
16  Dabur Almond Shampoo - With Almond-Vita Comple...  ...                                                 []
17  Herbal Essences Real Aloe & Bamboo Shampoo Sul...  ...                                                 []
18  Dove Intense Repair Shampoo For Damaged HairEn...  ...                                                 []
19  Dove Hair Fall Rescue Shampoo For Weak Hair Pr...  ...                                                 []
20  L'Oréal Professionnel Serie Expert Absolut Rep...  ...  ['Serie Expert Absolut Repair Shampoo', 'Serie...
21  Herbal Essences Argan Oil of Morocco SHAMPOO- ...  ...  ['Morocco Shampoo + Coconut Milk Conditioner',...
22  WOW Apple Cider Vinegar No Parabens & Sulphate...  ...  ['Shampoo', 'Shampoo + Activated Charcoal Face...
23  Dabur Vatika Health Shampoo with Henna & Amla ...  ...                                                 []
24  Dove Hair Fall Rescue Shampoo For Weak Hair Pr...  ...                                                 []
25  Schwarzkopf Professional Bc Peptide Repair Res...  ...  ['Rescue Treatment + Bc Q10', 'Rescue Treatmen...
26  Biotique Bio Green Apple Fresh Daily Purifying...  ...  ['Green Apple Shampoo', 'Green Apple Shampoo +...
27    The Body Shop BANANA Shampoo 250 ml (8.4 fl oz)  ...                                                 []
28  L'Occitane Damaged Hair Intensive Repairing Sh...  ...                                                 []
29       L'Oreal Paris Total Repair 5 Shampoo 1 Litre  ...  ['Shampoo', 'Shampoo & Conditioner', 'Shampoo ...
30       L'Oreal Paris Dream Lengths Shampoo 192.5 ml  ...                                                 []
31  L'Oreal Paris Extraordinary Clay Shampoo 704 m...  ...  ['Extraordinary Clay Shampoo + Condtioner', 'E...
32  Tresemme Hair Fall Defence Shampoo For Strong ...  ...  ['Shampoo', 'Shampoo 580ml + Conditioner 190ml...
33  Tresemme Hair Fall Defence Shampoo For Strong ...  ...                                                 []
34  Dove Hair Fall Rescue Shampoo For Weak Hair Pr...  ...                                                 []
35  Biotique Bio Kelp Protein Shampoo for Falling ...  ...             

In [ ]:
complete_data = []
for links in urls[:10]:
    print("-"*50)
    data = {}
    print(links)
    try: 
        product_info = web_scraping(links,data).Data()
        print(product_info)
        complete_data.append(product_info)
        time.sleep(5)
    except Exception as e:
        logging.error("Exception occurred", exc_info=True)
        print("-"*20 + " Exception " + "-"*20)
        print(links)
        print(e)

--------------------------------------------------
https://www.amazon.in/Dove-Intense-Repair-Shampoo-1L/dp/B07H9SV624/ref=sr_1_1_sspa?dchild=1&keywords=shampoo&qid=1622109833&smid=AT95IG9ONZD7S&sr=8-1-spons&psc=1&qualifier=1622109833&id=573937187656305&widgetName=sp_atf


[<ipython-input-17-5613e0f8996f>:42 -        product_title() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 38, in product_title
    title_value = title.string
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-17-5613e0f8996f>:138 -               rating() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 131, in rating
    rating = self.soup.find("i", attrs={'class': 'a-icon a-icon-star a-star-4-5'}).string.strip().replace(',', '')
AttributeError: 'NoneType' object has no attribute 'string'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 135, in rating
    rating = self.soup.find("span", attrs={'class': 'a-icon-alt'}).string.strip().replace(',', '')
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-17-5613e0f8996f>:149 -     

{'product Title': 'NA', 'brand': '', 'Products price': '', 'Offer_Count': '', 'StrikeThrough_Products_price': '', 'Fullfilled': '', 'Overall rating': 'NA', 'Total reviews': 'NA', 'Availability': 'NA', 'Category Tree': [], 'icons': [], 'Product_Details': {}, 'misc_info': '', 'bought_together': [], 'subscription_discount': '', 'variations': []}
--------------------------------------------------
https://www.amazon.in/Dove-Hair-Fall-Rescue-Shampoo/dp/B07H9T25WH/ref=sr_1_2_sspa?dchild=1&keywords=shampoo&qid=1622109833&sr=8-2-spons&psc=1&qualifier=1622109833&id=573937187656305&widgetName=sp_atf


[<ipython-input-17-5613e0f8996f>:42 -        product_title() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 38, in product_title
    title_value = title.string
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-17-5613e0f8996f>:138 -               rating() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 131, in rating
    rating = self.soup.find("i", attrs={'class': 'a-icon a-icon-star a-star-4-5'}).string.strip().replace(',', '')
AttributeError: 'NoneType' object has no attribute 'string'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 135, in rating
    rating = self.soup.find("span", attrs={'class': 'a-icon-alt'}).string.strip().replace(',', '')
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-17-5613e0f8996f>:149 -     

{'product Title': 'NA', 'brand': '', 'Products price': '', 'Offer_Count': '', 'StrikeThrough_Products_price': '', 'Fullfilled': '', 'Overall rating': 'NA', 'Total reviews': 'NA', 'Availability': 'NA', 'Category Tree': [], 'icons': [], 'Product_Details': {}, 'misc_info': '', 'bought_together': [], 'subscription_discount': '', 'variations': []}
--------------------------------------------------
https://www.amazon.in/LOreal-Professional-Absolute-Lipidium-Shampoo/dp/B0744GC2CK/ref=sr_1_3_sspa?dchild=1&keywords=shampoo&qid=1622109833&sr=8-3-spons&psc=1&qualifier=1622109833&id=573937187656305&widgetName=sp_atf


...

[<ipython-input-17-5613e0f8996f>:42 -        product_title() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 38, in product_title
    title_value = title.string
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-17-5613e0f8996f>:138 -               rating() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 131, in rating
    rating = self.soup.find("i", attrs={'class': 'a-icon a-icon-star a-star-4-5'}).string.strip().replace(',', '')
AttributeError: 'NoneType' object has no attribute 'string'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 135, in rating
    rating = self.soup.find("span", attrs={'class': 'a-icon-alt'}).string.strip().replace(',', '')
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-17-5613e0f8996f>:149 -     

--------------------------------------------------
https://www.amazon.in/Dove-Hair-Fall-Rescue-Shampoo/dp/B07H9T25WH/ref=sxin_7?asc_contentid=amzn1.osa.efe025f9-38a3-445b-9122-7932e6414502.A21TJRUUN4KGV.en_IN&asc_contenttype=article&ascsubtag=amzn1.osa.efe025f9-38a3-445b-9122-7932e6414502.A21TJRUUN4KGV.en_IN&creativeASIN=B07H9T25WH&cv_ct_cx=shampoo&cv_ct_id=amzn1.osa.efe025f9-38a3-445b-9122-7932e6414502.A21TJRUUN4KGV.en_IN&cv_ct_pg=search&cv_ct_we=asin&cv_ct_wn=osp-single-source-earns-comm&dchild=1&keywords=shampoo&linkCode=oas&pd_rd_i=B07H9T25WH&pd_rd_r=53736867-08b3-4018-b321-abbeacc866bd&pd_rd_w=bh9sK&pd_rd_wg=jH9wZ&pf_rd_p=b3b6fd96-9765-4b46-b334-5529fcb3a063&pf_rd_r=J5ZK69YNVKSCSSM9QR8W&qid=1622109833&sr=1-2-483c64d8-df78-4008-ae20-e69f683e58b1&tag=firstpost1610-21
{'product Title': 'NA', 'brand': '', 'Products price': '', 'Offer_Count': '', 'StrikeThrough_Products_price': '', 'Fullfilled': '', 'Overall rating': 'NA', 'Total reviews': 'NA', 'Availability': 'NA', 'Category Tree': [

[<ipython-input-17-5613e0f8996f>:42 -        product_title() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 38, in product_title
    title_value = title.string
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-17-5613e0f8996f>:138 -               rating() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 131, in rating
    rating = self.soup.find("i", attrs={'class': 'a-icon a-icon-star a-star-4-5'}).string.strip().replace(',', '')
AttributeError: 'NoneType' object has no attribute 'string'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "<ipython-input-17-5613e0f8996f>", line 135, in rating
    rating = self.soup.find("span", attrs={'class': 'a-icon-alt'}).string.strip().replace(',', '')
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-17-5613e0f8996f>:149 -     

{'product Title': 'NA', 'brand': '', 'Products price': '', 'Offer_Count': '', 'StrikeThrough_Products_price': '', 'Fullfilled': '', 'Overall rating': 'NA', 'Total reviews': 'NA', 'Availability': 'NA', 'Category Tree': [], 'icons': [], 'Product_Details': {}, 'misc_info': '', 'bought_together': [], 'subscription_discount': '', 'variations': []}
--------------------------------------------------
https://www.amazon.in/WOW-Vinegar-Sulphate-Parabens-Shampoo/dp/B01M9EB7ZK/ref=sr_1_5?dchild=1&keywords=shampoo&qid=1622109833&smid=AT95IG9ONZD7S&sr=8-5


KeyboardInterrupt: ignored

In [ ]:
complete_data = []
for links in urls[:1000]:
    print("-"*50)
    data = {}
    print(links)
    try: 
        product_info = web_scraping(links,data).Data()
        print(product_info)
        complete_data.append(product_info)
        time.sleep(5)
    except Exception as e:
        logging.error("Exception occurred", exc_info=True)
        print("-"*20 + " Exception " + "-"*20)
        print(links)
        print(e)

--------------------------------------------------
https://www.amazon.in/Dove-Intense-Repair-Shampoo-1L/dp/B07H9SV624/ref=sr_1_1_sspa?dchild=1&keywords=shampoo&qid=1622109833&smid=AT95IG9ONZD7S&sr=8-1-spons&psc=1&qualifier=1622109833&id=573937187656305&widgetName=sp_atf


[<ipython-input-20-4b4ff865b1dd>:215 -      product_details() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-20-4b4ff865b1dd>", line 212, in product_details
    prod_feat[feat[0]] = feat[1]
IndexError: list index out of range
[<ipython-input-20-4b4ff865b1dd>:275 -           variations() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-20-4b4ff865b1dd>", line 269, in variations
    variations_list = variations_div.find_all(
AttributeError: 'NoneType' object has no attribute 'find_all'


₹ 468.00
{'product Title': 'Dove Intense Repair Shampoo For Damaged HairEnriched with Fiber Actives Repairs Hair Damage  Makes Hair Smooth And Strong 1 Ltr', 'brand': 'Dove', 'Products price': '468.00', 'Offer_Count': '4', 'StrikeThrough_Products_price': '690.00', 'Fullfilled': 'Fulfilled', 'Overall rating': '4.4 out of 5 stars', 'Total reviews': '12435 ratings', 'Availability': 'In stock on June 12 2021.', 'Category Tree': [], 'icons': ['Pay on Delivery', 'Not Returnable', 'Amazon Delivered', 'No-Contact Delivery'], 'Product_Details': None, 'misc_info': "Important informationDirections:Completely soak your hair and massage your shampoo gently over your scalp. Rinse it out well. Usually rinse and repeat? For daily shampooing the rinse and repeat rule isn't actually necessary (unless you've been trigger-happy with the hairspray), so just once will do", 'bought_together': ['Dove Intense Repair Shampoo For Damaged Hair,Enriched with Fiber Actives, Repairs Hair Damage , Makes Hair Smooth A

[<ipython-input-20-4b4ff865b1dd>:215 -      product_details() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-20-4b4ff865b1dd>", line 212, in product_details
    prod_feat[feat[0]] = feat[1]
IndexError: list index out of range


₹ 468.00
{'product Title': 'Dove Hair Fall Rescue Shampoo For Weak Hair Prone To Hairfall Deeply Nourishes From Roots Up And Reduces Hair Fall 1 Ltr', 'brand': 'Dove', 'Products price': '468.00', 'Offer_Count': '4', 'StrikeThrough_Products_price': '580.00', 'Fullfilled': 'Fulfilled', 'Overall rating': '4.4 out of 5 stars', 'Total reviews': '9662 ratings', 'Availability': 'In stock on June 12 2021.', 'Category Tree': [], 'icons': ['Pay on Delivery', 'Not Returnable', 'Amazon Delivered', 'No-Contact Delivery'], 'Product_Details': None, 'misc_info': 'Important informationDirections:Store in cool & dry place away from sunlight', 'bought_together': ['Dove Hair Fall Rescue Shampoo For Weak Hair Prone To Hairfall, Deeply Nourishes From Roots Up And Reduces Hair Fall, 1 Ltr'], 'subscription_discount': '5%', 'variations': []}
--------------------------------------------------
https://www.amazon.in/LOreal-Professional-Absolute-Lipidium-Shampoo/dp/B0744GC2CK/ref=sr_1_3_sspa?dchild=1&keywords=sham

...

{'product Title': 'NA', 'brand': 'NA', 'Products price': 'NA', 'Offer_Count': '', 'StrikeThrough_Products_price': '', 'Fullfilled': 'NA', 'Overall rating': 'NA', 'Total reviews': 'NA', 'Availability': 'NA', 'Category Tree': 'NA', 'icons': [], 'Product_Details': 'NA', 'misc_info': 'NA', 'bought_together': 'NA', 'subscription_discount': 'NA', 'variations': 'NA'}
--------------------------------------------------
https://www.amazon.in/LOreal-Paris-Dream-Lengths-Shampoo/dp/B08T2VT7B8/ref=sr_1_2412_sspa?dchild=1&keywords=shampoo&qid=1622111178&sr=8-2412-spons&psc=1&qualifier=1622111178&id=4923114351952913&widgetName=sp_btf


[<ipython-input-20-4b4ff865b1dd>:46 -        product_title() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-20-4b4ff865b1dd>", line 41, in product_title
    title_value = title.string
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-20-4b4ff865b1dd>:64 -                brand() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-20-4b4ff865b1dd>", line 59, in brand
    title = title.find("span", attrs={'class': 'a-size-base'})
AttributeError: 'NoneType' object has no attribute 'find'
[<ipython-input-20-4b4ff865b1dd>:80 -        product_price() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-20-4b4ff865b1dd>", line 74, in product_price
    price = self.soup.find("span", attrs={'id': price_tag}).string.strip().replace(',', '')
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-20-4b4ff865b1dd>:95 -               offers() ] Exception occurred
Traceba

{'product Title': 'NA', 'brand': 'NA', 'Products price': 'NA', 'Offer_Count': '', 'StrikeThrough_Products_price': '', 'Fullfilled': 'NA', 'Overall rating': 'NA', 'Total reviews': 'NA', 'Availability': 'NA', 'Category Tree': 'NA', 'icons': [], 'Product_Details': 'NA', 'misc_info': 'NA', 'bought_together': 'NA', 'subscription_discount': 'NA', 'variations': 'NA'}
--------------------------------------------------
https://www.amazon.in/LOreal-Paris-Dream-Lengths-Shampoo/dp/B08T2VT7B8/ref=sr_1_2449_sspa?dchild=1&keywords=shampoo&qid=1622111197&sr=8-2449-spons&psc=1&qualifier=1622111197&id=2997318497738569&widgetName=sp_atf_next


[<ipython-input-20-4b4ff865b1dd>:46 -        product_title() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-20-4b4ff865b1dd>", line 41, in product_title
    title_value = title.string
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-20-4b4ff865b1dd>:64 -                brand() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-20-4b4ff865b1dd>", line 59, in brand
    title = title.find("span", attrs={'class': 'a-size-base'})
AttributeError: 'NoneType' object has no attribute 'find'
[<ipython-input-20-4b4ff865b1dd>:80 -        product_price() ] Exception occurred
Traceback (most recent call last):
  File "<ipython-input-20-4b4ff865b1dd>", line 74, in product_price
    price = self.soup.find("span", attrs={'id': price_tag}).string.strip().replace(',', '')
AttributeError: 'NoneType' object has no attribute 'string'
[<ipython-input-20-4b4ff865b1dd>:95 -               offers() ] Exception occurred
Traceba

{'product Title': 'NA', 'brand': 'NA', 'Products price': 'NA', 'Offer_Count': '', 'StrikeThrough_Products_price': '', 'Fullfilled': 'NA', 'Overall rating': 'NA', 'Total reviews': 'NA', 'Availability': 'NA', 'Category Tree': 'NA', 'icons': [], 'Product_Details': 'NA', 'misc_info': 'NA', 'bought_together': 'NA', 'subscription_discount': 'NA', 'variations': 'NA'}


In [ ]:
web_scraping('https://www.amazon.in/Mamaearth-Shampoo-Keratin-Damaged-Frizzy/dp/B08ZSFMGW1/ref=sr_1_17?dchild=1&keywords=shampoo&qid=1622109910&smid=A61C6NUFGVGS7&sr=8-17',{}).product_title()

'Mamaearth Rice Water Shampoo With Rice Water & Keratin For Damaged Dry and Frizzy Hair – 250ml'